# Tutorial

This is a run-through tutorial intended to display variety of methods for combining datasets using the `kerchunk.combine.MultiZarrtoZarr` API. 

Initially we create a pair of single file jsons for two ERA5 variables using `Kerchunk.hdf.SingleHdf5ToZarr`. This dataset is free to access and so it should be possible to replicate this workflow on a local machine without credentials.



## Single file JSONs

The `Kerchunk.hdf.SingleHdf5ToZarr` is used to create a single `.json` reference file for each file url passed to it. Here we use it to create a number of `.json` reference files pointing towrds the ERA5 pubic dataset on [AWS](https://registry.opendata.aws/ecmwf-era5/). We will compute a number of different times and variables to demonstrate different methods of combining them.

The Kerchunk package is still in a devolpment phase and so changes frequently. Installing directly from the source code is recommended. 

In [ ]:
!pip install git+https://github.com/fsspec/kerchunk

Here we are considering Netcdf4 files and so use the kerchunk `hdf` module. Support for `fits`, `grib2`, `tiff`, `netCDF3` and `zarr` are available in other kerchunk modules. Alternatively it is also possible to manually create reference jsons for more specific cases. The Earth Big Data [example](https://github.com/fsspec/kerchunk/blob/main/examples/earthbigdata.ipynb) provides a demonstration of this.

In [1]:
from kerchunk.hdf import SingleHdf5ToZarr 
import fsspec

Using fsspec to create a pythonic filesystem, provides a convenient way to manage file urls.

In [2]:
fs = fsspec.filesystem('s3', anon=True) #S3 file system to manage ERA5 files
flist = (fs.glob('s3://era5-pds/2020/*/data/air_pressure_at_mean_sea_level.nc')[:2]
        + fs.glob('s3://era5-pds/2020/*/data/*sea_surface_temperature.nc')[:2])

In [3]:
fs2 = fsspec.filesystem('')  #local file system to save final jsons to

In [4]:
from pathlib import Path
import os
import ujson

so = dict(mode='rb', anon=True, default_fill_cache=False, default_cache_type='first') # args to fs.open()
# default_fill_cache=False avoids caching data in between file chunks to lowers memory usage.

def gen_json(file):
    with fs.open(file, **so) as infile:
        h5chunks = SingleHdf5ToZarr(infile, file, inline_threshold=300) 
        # inline threshold adjusts the Size below which binary blocks are included directly in the output
        # a higher inline threshold can result in a larger json file but faster loading time
        variable = file.split('/')[-1].split('.')[0]
        month = file.split('/')[2] 
        outf = f'{month}_{variable}.json' #file name to save json to
        with fs2.open(outf, 'wb') as f:
            f.write(ujson.dumps(h5chunks.translate()).encode());

ERA5-pds is located in us-west-2 and so depending on where this computation is taking place the time taken can vary dramatically and is likely to be faster than this.

In [16]:
%%time
for file in flist:
    gen_json(file)

CPU times: user 30.4 s, sys: 4.74 s, total: 35.1 s
Wall time: 14min 44s


The `.json` files we have generated can now be opened, with no latency, as virtual datasets through xarray. To achieve this it is first neccessary to create a mapping of the reference file using `fsspec`. Here specifying that the reference json is pointing to files stored on AWS. 

In [5]:
import xarray as xr

In [6]:
%%time
fs_ = fsspec.filesystem("reference", fo='01_air_pressure_at_mean_sea_level.json', ref_storage_args={'skip_instance_cache':True},
                       remote_protocol='s3', remote_options={'anon':True})
m = fs_.get_mapper("")
ds = xr.open_dataset(m, engine="zarr", backend_kwargs={'consolidated':False}, chunks={})
print(ds)

<xarray.Dataset>
Dimensions:                         (time0: 744, lat: 721, lon: 1440)
Coordinates:
  * lat                             (lat) float32 90.0 89.75 ... -89.75 -90.0
  * lon                             (lon) float32 nan 0.25 0.5 ... 359.5 359.8
  * time0                           (time0) datetime64[ns] 2020-01-01 ... 202...
Data variables:
    air_pressure_at_mean_sea_level  (time0, lat, lon) float32 dask.array<chunksize=(24, 100, 100), meta=np.ndarray>
Attributes:
    institution:  ECMWF
    source:       Reanalysis
    title:        ERA5 forecasts
CPU times: user 162 ms, sys: 17.4 ms, total: 180 ms
Wall time: 235 ms


## Combine multiple kerchunk'd datasets into a single logical aggregate dataset

The `Kerchunk.combine.MultiZarrtoZarr` method combines the `.json` reference files generated above to create a single virtual dataset, such that one reference file maps to all of the chunks in the individual files.

In [7]:
from kerchunk.combine import MultiZarrToZarr

MultiZarrtoZarr provides a number of convenience methods to combine reference files. The simplest is to concatenate along a specified dimension using the `concat_dims` argument, Time0 in this instance. Specifying the coordinate that are identical across the files using the `identical_dims` argument can speed up the computation.

In [8]:
json_list = fs2.glob("*_air_pressure_at_mean_sea_level.json")

mzz = MultiZarrToZarr(json_list,                
    remote_protocol='s3',
    remote_options={'anon':True},
    concat_dims=['time0'],
    identical_dims = ['lat', 'lon'])

d = mzz.translate()

with fs2.open('air_pressure_at_mean_sea_level_combined.json', 'wb') as f:
    f.write(ujson.dumps(d).encode())

The reference json we have just generated can now be opened to reveal a single virtual dataset spanning both the input files. Again with no latency.

In [9]:
%%time
m = fsspec.filesystem("reference", fo=d).get_mapper("")
ds = xr.open_dataset(m, engine="zarr", consolidated=False)
print(ds)

<xarray.Dataset>
Dimensions:                         (time0: 1440, lat: 721, lon: 1440)
Coordinates:
  * lat                             (lat) float32 90.0 89.75 ... -89.75 -90.0
  * lon                             (lon) float32 nan 0.25 0.5 ... 359.5 359.8
  * time0                           (time0) datetime64[ns] 2020-01-01 ... 202...
Data variables:
    air_pressure_at_mean_sea_level  (time0, lat, lon) float32 ...
Attributes:
    institution:  ECMWF
    source:       Reanalysis
    title:        ERA5 forecasts
CPU times: user 42.3 ms, sys: 128 µs, total: 42.5 ms
Wall time: 40.9 ms


### Using coo_map

For more complex use cases, such as when the dimension along which we would like to concatenate is not already in the dataset, or when considering datasets from across an ensemble we can use the `coo_map` argument to create a new dimension

In [10]:
new_dims = ['a' , 'b']

mzz = MultiZarrToZarr(json_list,                
    remote_protocol='s3',
    remote_options={'anon':True},
    coo_map = {'new_dimension':new_dims},
    concat_dims=['new_dimension'],
    identical_dims = ['lat', 'lon']
)

d = mzz.translate()

In [11]:
m = fsspec.filesystem("reference", fo=d).get_mapper("")
ds = xr.open_dataset(m, engine="zarr", consolidated=False)
print(ds)

<xarray.Dataset>
Dimensions:                         (new_dimension: 2, time0: 744, lat: 721,
                                     lon: 1440)
Coordinates:
  * lat                             (lat) float32 90.0 89.75 ... -89.75 -90.0
  * lon                             (lon) float32 nan 0.25 0.5 ... 359.5 359.8
  * new_dimension                   (new_dimension) object 'a' 'b'
  * time0                           (time0) datetime64[ns] 2020-01-01 ... 202...
Data variables:
    air_pressure_at_mean_sea_level  (new_dimension, time0, lat, lon) float32 ...
Attributes:
    institution:  ECMWF
    source:       Reanalysis
    title:        ERA5 forecasts


For more complex uses it is also possible to pass in a compiled `regex` function which operates on the input file url's to generate a unique variable for each file.

In [12]:
import re
ex = re.compile(r'.*(\d+)_air')

In [13]:
ex.match(json_list[0]).groups()[0]

'1'

In [14]:
mzz = MultiZarrToZarr(json_list,                
    remote_protocol='s3',
    remote_options={'anon':True},
    coo_map = {'new_dimension':ex},
    concat_dims=['new_dimension'],
    identical_dims = ['lat', 'lon']
)

d = mzz.translate()

In [15]:
m = fsspec.filesystem("reference", fo=d).get_mapper("")
ds = xr.open_dataset(m, engine="zarr", consolidated=False)
print(ds)

<xarray.Dataset>
Dimensions:                         (new_dimension: 2, time0: 744, lat: 721,
                                     lon: 1440)
Coordinates:
  * lat                             (lat) float32 90.0 89.75 ... -89.75 -90.0
  * lon                             (lon) float32 nan 0.25 0.5 ... 359.5 359.8
  * new_dimension                   (new_dimension) object '1' '2'
  * time0                           (time0) datetime64[ns] 2020-01-01 ... 202...
Data variables:
    air_pressure_at_mean_sea_level  (new_dimension, time0, lat, lon) float32 ...
Attributes:
    institution:  ECMWF
    source:       Reanalysis
    title:        ERA5 forecasts


Similarly we can map each file to a new variable using the special `var` character in coo_map. Here we use the same `regex` function but instead map these as new variables.

In [16]:
mzz = MultiZarrToZarr(json_list,                
    remote_protocol='s3',
    remote_options={'anon':True},
    coo_map = {"var":ex},
    concat_dims=['time0'],
    identical_dims = ['lat', 'lon']
)

d = mzz.translate()

In [17]:
m = fsspec.filesystem("reference", fo=d).get_mapper("")
ds = xr.open_dataset(m, engine="zarr", consolidated=False)
print(ds)

<xarray.Dataset>
Dimensions:  (time0: 1440, lat: 721, lon: 1440)
Coordinates:
  * lat      (lat) float32 90.0 89.75 89.5 89.25 ... -89.25 -89.5 -89.75 -90.0
  * lon      (lon) float32 nan 0.25 0.5 0.75 1.0 ... 359.0 359.2 359.5 359.8
  * time0    (time0) datetime64[ns] 2020-01-01 ... 2020-02-29T23:00:00
Data variables:
    1        (time0, lat, lon) float32 ...
    2        (time0, lat, lon) float32 ...
Attributes:
    institution:  ECMWF
    source:       Reanalysis
    title:        ERA5 forecasts


Another special character in `coo_map` is `attr:`. This allows the user to access variables from the file attributes.

In [18]:
mzz = MultiZarrToZarr(json_list,                
    remote_protocol='s3',
    remote_options={'anon':True},
    coo_map = {"var":"attr:institution"},
    concat_dims=['time0'],
    identical_dims = ['lat', 'lon']
)

d = mzz.translate()

In [19]:
m = fsspec.filesystem("reference", fo=d).get_mapper("")
ds = xr.open_dataset(m, engine="zarr", consolidated=False)
print(ds)

<xarray.Dataset>
Dimensions:  (time0: 1440, lat: 721, lon: 1440)
Coordinates:
  * lat      (lat) float32 90.0 89.75 89.5 89.25 ... -89.25 -89.5 -89.75 -90.0
  * lon      (lon) float32 nan 0.25 0.5 0.75 1.0 ... 359.0 359.2 359.5 359.8
  * time0    (time0) datetime64[ns] 2020-01-01 ... 2020-02-29T23:00:00
Data variables:
    ECMWF    (time0, lat, lon) float32 ...
Attributes:
    institution:  ECMWF
    source:       Reanalysis
    title:        ERA5 forecasts


Similarly the special charactar `vattr:{var}:` allows access to variable attributes. Here renaming the variable to instead use it's short name. There are a number of other special characters for `coo_map` documented in the [API reference](https://fsspec.github.io/kerchunk/reference.html#kerchunk.combine.MultiZarrToZarr)

In [20]:
mzz = MultiZarrToZarr(json_list,                
    remote_protocol='s3',
    remote_options={'anon':True},
    coo_map = {"var":"vattr:air_pressure_at_mean_sea_level:shortNameECMWF"},
    concat_dims=['time0'],
    identical_dims = ['lat', 'lon']
)

d = mzz.translate()

In [21]:
m = fsspec.filesystem("reference", fo=d).get_mapper("")
ds = xr.open_dataset(m, engine="zarr", consolidated=False)
print(ds)

<xarray.Dataset>
Dimensions:  (lat: 721, lon: 1440, time0: 1440)
Coordinates:
  * lat      (lat) float32 90.0 89.75 89.5 89.25 ... -89.25 -89.5 -89.75 -90.0
  * lon      (lon) float32 nan 0.25 0.5 0.75 1.0 ... 359.0 359.2 359.5 359.8
  * time0    (time0) datetime64[ns] 2020-01-01 ... 2020-02-29T23:00:00
Data variables:
    msl      (time0, lat, lon) float32 ...
Attributes:
    institution:  ECMWF
    source:       Reanalysis
    title:        ERA5 forecasts


### Merging variables across jsons

To merge two variables into a single dataset using the `Kerchunk.combine.MultiZarrtoZarr` method we can simply concatenate along an existing dimension.

In [22]:
json_list = fs2.glob("01_sea_surface_temperature.json") + fs2.glob("01_air_pressure_at_mean_sea_level.json")

mzz = MultiZarrToZarr(json_list,                
    remote_protocol='s3',
    remote_options={'anon':True},
    concat_dims=['time0'],
    identical_dims = ['lat', 'lon'])

d = mzz.translate()

In [23]:
m = fsspec.filesystem("reference", fo=d).get_mapper("")
ds = xr.open_dataset(m, engine="zarr", consolidated=False)
print(ds)

<xarray.Dataset>
Dimensions:                         (time0: 744, lat: 721, lon: 1440)
Coordinates:
  * lat                             (lat) float32 90.0 89.75 ... -89.75 -90.0
  * lon                             (lon) float32 nan 0.25 0.5 ... 359.5 359.8
  * time0                           (time0) datetime64[ns] 2020-01-01 ... 202...
Data variables:
    air_pressure_at_mean_sea_level  (time0, lat, lon) float32 ...
    sea_surface_temperature         (time0, lat, lon) float32 ...
Attributes:
    institution:  ECMWF
    source:       Reanalysis
    title:        ERA5 forecasts


This however iterates across the concatenating variable in both datasets and thus can be slow, if we know the two datasets share identical coordinates we can simply add the relevant dictionary items from the one variable to the other. The below will soon be available as a convenience function within `Kerchunk.combine`

In [24]:
with fs2.open(json_list[0], 'rb') as f:
    var_1 = ujson.load(f)

with fs2.open(json_list[1], 'rb') as f:
    var_2 = ujson.load(f)

var_1['refs'].update(var_2['refs'])

with fs2.open('vars_combined.json', 'wb') as f:
    f.write(ujson.dumps(var_1).encode())

In [25]:
m = fsspec.filesystem("reference", fo=var_1).get_mapper("")
ds = xr.open_dataset(m, engine="zarr", consolidated=False)
print(ds)

<xarray.Dataset>
Dimensions:                         (time0: 744, lat: 721, lon: 1440)
Coordinates:
  * lat                             (lat) float32 90.0 89.75 ... -89.75 -90.0
  * lon                             (lon) float32 nan 0.25 0.5 ... 359.5 359.8
  * time0                           (time0) datetime64[ns] 2020-01-01 ... 202...
Data variables:
    air_pressure_at_mean_sea_level  (time0, lat, lon) float32 ...
    sea_surface_temperature         (time0, lat, lon) float32 ...
Attributes:
    institution:  ECMWF
    source:       Reanalysis
    title:        ERA5 forecasts


### Preprocessing

Pre-process can be used to apply arbitrary functions to the refs item in the input jsons before combining. In this case we use preprocessing to drop the `air_pressure_at_mean_sea_level` variable before combining `sea_surface_temperature` with a json containing data for the following month.

In [26]:
def pre_process(refs):
    for k in list(refs):
        if k.startswith('air_pressure_at_mean_sea_level'):
            refs.pop(k)
    return refs

In [27]:
json_list = fs2.glob("vars_combined.json") + fs2.glob("02_sea_surface_temperature.json")

In [28]:
mzz = MultiZarrToZarr(json_list,                
    remote_protocol='s3',
    remote_options={'anon':True},
    concat_dims=['time0'],
    identical_dims = ['lat', 'lon'],
    preprocess = pre_process)

d = mzz.translate()

In [29]:
with fs2.open('sea_surface_temperature_combined.json', 'wb') as f:
    f.write(ujson.dumps(d).encode())

In [30]:
m = fsspec.filesystem("reference", fo=d).get_mapper("")
ds = xr.open_dataset(m, engine="zarr", consolidated=False)
print(ds)

<xarray.Dataset>
Dimensions:                  (lat: 721, lon: 1440, time0: 1440)
Coordinates:
  * lat                      (lat) float32 90.0 89.75 89.5 ... -89.75 -90.0
  * lon                      (lon) float32 nan 0.25 0.5 ... 359.2 359.5 359.8
  * time0                    (time0) datetime64[ns] 2020-01-01 ... 2020-02-29...
Data variables:
    sea_surface_temperature  (time0, lat, lon) float32 ...
Attributes:
    institution:  ECMWF
    source:       Reanalysis
    title:        ERA5 forecasts


### Postprocessing

Similarly post-process can be used to apply an arbitrary function to the final dictionary before returning.
A known issue with this partcular dataset is that no fill value has been assigned to the lat and lon coordinates and thus default to 0, here we use post process to change the zarr fill_value attribute by opening the final json as a zarr store. 

Changing the fill_values could also be achieved by editing the final json through string manipulations or even a simple find and replace through an IDE.

In [31]:
import zarr
def modify_fill_value(out):
    out_ = zarr.open(out)
    out_.lon.fill_value = -999
    out_.lat.fill_value = -999
    return out

def postprocess(out):
    out = modify_fill_value(out)
    return out

In [32]:
json_list = fs2.glob("air_pressure_at_mean_sea_level_combined.json") + fs2.glob("sea_surface_temperature_combined.json")

mzz = MultiZarrToZarr(json_list,                
    remote_protocol='s3',
    remote_options={'anon':True},
    concat_dims=['time0'],
    identical_dims = ['lat', 'lon'],
    postprocess = postprocess)

d = mzz.translate()

In [33]:
with fs2.open('combined.json', 'wb') as f:
    f.write(ujson.dumps(d).encode())

In [34]:
m = fsspec.filesystem("reference", fo=d).get_mapper("")
ds = xr.open_dataset(m, engine="zarr", consolidated=False)
print(ds)

<xarray.Dataset>
Dimensions:                         (time0: 1440, lat: 721, lon: 1440)
Coordinates:
  * lat                             (lat) float32 90.0 89.75 ... -89.75 -90.0
  * lon                             (lon) float32 0.0 0.25 0.5 ... 359.5 359.8
  * time0                           (time0) datetime64[ns] 2020-01-01 ... 202...
Data variables:
    air_pressure_at_mean_sea_level  (time0, lat, lon) float32 ...
    sea_surface_temperature         (time0, lat, lon) float32 ...
Attributes:
    institution:  ECMWF
    source:       Reanalysis
    title:        ERA5 forecasts


## Using the output

This is what a user of the generated dataset would do. This person does not need to have kerchunk installed, or even h5py (the library we used to initially scan the files). 

Here we open a previously generated `.json` reference file that contains 10 ERA5 variables across a 2 and a half year span.

The sidecar file has been compressed, from the original 125MB to 14Mb, using zstd to ensure the file is small enough to store on github. The below code block decompresses it.

In [35]:
import zstandard
with open('ERA5_2020_2022_multivar.json.zst', 'rb') as compressed:
    decomp = zstandard.ZstdDecompressor()
    with open('kerchunk.json', 'wb') as destination:
        decomp.copy_stream(compressed, destination)

In [5]:
%%time
fs = fsspec.filesystem("reference", fo='kerchunk.json', ref_storage_args={'skip_instance_cache':True},
                       remote_protocol='s3', remote_options={'anon':True})
m = fs.get_mapper("")
ds = xr.open_dataset(m, engine="zarr", backend_kwargs={'consolidated':False}, chunks={'time0':96})
print(ds)

<xarray.Dataset>
Dimensions:                               (time0: 21168, lat: 721, lon: 1440)
Coordinates:
  * lat                                   (lat) float32 90.0 89.75 ... -90.0
  * lon                                   (lon) float32 0.0 0.25 ... 359.5 359.8
  * time0                                 (time0) datetime64[ns] 2020-01-01 ....
Data variables:
    air_pressure_at_mean_sea_level        (time0, lat, lon) float32 dask.array<chunksize=(96, 100, 100), meta=np.ndarray>
    air_temperature_at_2_metres           (time0, lat, lon) float32 dask.array<chunksize=(96, 100, 100), meta=np.ndarray>
    dew_point_temperature_at_2_metres     (time0, lat, lon) float32 dask.array<chunksize=(96, 100, 100), meta=np.ndarray>
    eastward_wind_at_100_metres           (time0, lat, lon) float32 dask.array<chunksize=(96, 100, 100), meta=np.ndarray>
    eastward_wind_at_10_metres            (time0, lat, lon) float32 dask.array<chunksize=(96, 100, 100), meta=np.ndarray>
    lwe_thickness_of_surfac

In [6]:
ds = ds.sel(time0 = '2021-01-01T00:00:00')

import hvplot.xarray
import panel as pn
import cartopy.crs as ccrs

variables = list(ds.data_vars)

sel = pn.widgets.Select(options=variables, name='Data Variable')
pn.Column(sel, ds.hvplot.image(z=sel, cmap = 'viridis', 
                               coastline=True,projection=ccrs.Orthographic(25, 5),
                               global_extent=True, frame_height=500))

Column
    [0] Select(name='Data Variable', options=['air_pressure_at_mean_sea...], value='air_pressure_at_mean_sea_...)
    [1] ParamFunction(function)